# <font color = 'green'> Read the raw data and do priliminary text cleaning.</font>

In [2]:
from installdatabase import *
import os
import pickle
import tqdm as notebook_tqdm

path = r'C:\Users\zhaoz\Desktop\bigdata\finalproject\data'

#read raw data
f = open(path + os.sep + 'fund_objectives_strategy_raw.pkl','rb')
fund_objectives_strategy_raw = pickle.load(f)

In [3]:
import re
#%pip install nltk
from nltk.corpus import stopwords

cachedStopWords = stopwords.words("english") #caching the stopwords object to boost the processing speed

def word_reduction(target_string_list):
    main_texts = []
    for i in target_string_list:
        #lower case
        lower_text = str.lower(i)
        #remove special characters
        cleaned_text = re.sub('[^A-Za-z]+', ' ', lower_text).replace("_", '') 
        #remove stopwords
        cleaned_text = ' '.join([word for word in cleaned_text.split() if word not in cachedStopWords])
        main_texts.append(cleaned_text)
    return main_texts

cleaned_text = word_reduction(fund_objectives_strategy_raw['strategy'])#convert the dataframe to list

In [4]:
cleaned_text[0:5]

['achieve objective fund invest primarily equities including common preferred stocks warrants similar rights purchase companys securities convertible securities issued non u companies fund may invest securities traded mature markets example japan germany france countries whose economies still developing sometimes called emerging markets fund particularly seeks companies financial strength stability strong management fundamental value fundamental value term commonly used value investors refer estimate value educated buyer would place company whole normally fund invests least net assets plus borrowings investment purposes foreign securities counts relevant derivative positions towards assets allocation values position price held funds books fund may invest total assets debt instruments investment decisions fund made without regard capitalization size companies invests fund may invest size company including large medium smaller companies fund may invest fixed income instruments without re

In [6]:
len(cleaned_text)

6469

In [16]:
with open(path + os.sep + 'cleaned_text.pkl','wb') as f1:
    pickle.dump(cleaned_text, f1)

# <font color = 'green'> Define the model.

## <font color = 'green'> Define the model and tokenizer.</font>

Here we use an established model BERT ESG pretrained by Mukut Mukherjee.

*Source:*</br>
https://huggingface.co/nbroad/ESG-BERT</br>
</font>

In [19]:
#download pretrained esg bert model

#update to latest version

#%pip install -U transformers
#%pip install -U huggingface_hub

import torch
from torch.nn import functional as F
from transformers import AutoTokenizer, AutoModelForSequenceClassification

#define tokenizer
tokenizer = AutoTokenizer.from_pretrained('deepset/sentence_bert', ignore_mismatched_sizes=True)

#use GPU
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
#define model
model = AutoModelForSequenceClassification.from_pretrained('deepset/sentence_bert', ignore_mismatched_sizes=True)
model.to(device)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at deepset/sentence_bert and are newly initialized because the shapes did not match:
- classifier.weight: found shape torch.Size([3, 2304]) in the checkpoint and torch.Size([2, 768]) in the model instantiated
- classifier.bias: found shape torch.Size([3]) in the checkpoint and torch.Size([2]) in the model instantiated
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12,

In [26]:
esg_related_issues = ['violation of national legislation', \
 'corruption, bribery, extortion and money laundering', \
 'fraud', \
 'social discrimination', \
 'human rights abuses and corporate complicity', \
 'products (health and environmental issues)', \
 'occupational health and safety issues', \
 'poor employment conditions', \
 'supply chain issues', \
 'impacts on communities', \
 'impacts on landscapes, ecosystems and biodiversity', \
 'discrimination in employment', \
 'misleading communication', \
 'local pollution', \
 'climate change, ghg emissions, and global pollution', \
 'waste issues', \
 'local participation issues', \
 'executive compensation issues', \
 'controversial products and services', \
 'animal mistreatment', \
 'tax evasion', \
 'overuse and wasting of resources',
 'forced labor', \
 'child labor', \
 'anti-competitive practices', \
 'freedom of association and collective bargaining', \
 'tax optimization', \
 'violation of international standards', \
 'other esg issues']

ESG Bert

In [34]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device

device(type='cpu')

In [32]:
# tested in transformers==4.18.0 
from transformers import BertTokenizer, BertForSequenceClassification, pipeline

finbert = BertForSequenceClassification.from_pretrained('nbroad/ESG-BERT')
tokenizer = BertTokenizer.from_pretrained('nbroad/ESG-BERT')
nlp = pipeline("text-classification", model=finbert, tokenizer=tokenizer)
results = nlp(cleaned_text[0:10])
print(results, '</n>')

[{'label': 'Systemic_Risk_Management', 'score': 0.36517152190208435}, {'label': 'Management_Of_Legal_And_Regulatory_Framework', 'score': 0.4572378396987915}, {'label': 'Competitive_Behavior', 'score': 0.32040008902549744}, {'label': 'Systemic_Risk_Management', 'score': 0.7242156863212585}, {'label': 'Systemic_Risk_Management', 'score': 0.5584273934364319}, {'label': 'Systemic_Risk_Management', 'score': 0.6860199570655823}, {'label': 'Customer_Welfare', 'score': 0.2816471457481384}, {'label': 'Systemic_Risk_Management', 'score': 0.3561249077320099}, {'label': 'Systemic_Risk_Management', 'score': 0.689927339553833}, {'label': 'Systemic_Risk_Management', 'score': 0.5327144861221313}] </n>


## <font color = 'green'> Fine tuning the pretrained model.
*Source:*</br>
https://github.com/mukut03/ESG-BERT </br>
https://github.com/dtolk/multilabel-BERT </br>
https://zhuanlan.zhihu.com/p/66440354
</font>

In [ ]:
#%pip install torchserve torch-model-archiver
#%pip install torchvision 
#%pip install transformers

# <font color = 'green'> Load the dataset.
</font>

In [15]:
#classify string in the list cleaned text by bert model
def bert_classification(text_list):
    for s in text_list:
        #tokenize the string
        inputs = tokenizer(s, truncation=True, return_tensors="pt", padding=True)
        #use GPU
        inputs.to(device)
        #classify the string
        outputs = model(**inputs)
        #get the predicted label
        predicted = torch.argmax(outputs.logits, dim=1)
        print(predicted) 

predicted = bert_classification(cleaned_text)

tensor([18])
tensor([12])
tensor([4])
tensor([18])
tensor([18])
tensor([18])
tensor([6])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([12])
tensor([4])
tensor([18])
tensor([18])
tensor([12])
tensor([18])
tensor([4])
tensor([18])
tensor([4])
tensor([18])
tensor([18])
tensor([4])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([12])
tensor([4])
tensor([18])
tensor([12])
tensor([18])
tensor([4])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([18])
tensor([12])
tensor([12])
tensor([12])
tensor([12])
tensor([12])
tensor([12])
tensor([12])
tensor([12])
tensor([12])
tensor([12])
tensor([12])
tensor([12])
tensor(

KeyboardInterrupt: 

In [26]:
def word_tokenization(target_string_list):
    tokenized_words = []
    for i in target_string_list:
        word_tokens = tokenizer.tokenize(i, max_length=512)
        tokenized_words.append(word_tokens)
    return tokenized_words

tokenized_related_issues = word_tokenization(cleaned_text)

Truncation was not explicitly activated but `max_length` is provided a specific value, please use `truncation=True` to explicitly truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.


In [27]:
tokenized_related_issues

[['to',
  'achieve',
  'objective',
  'fund',
  'invest',
  'primarily',
  'e',
  '##qui',
  '##ties',
  'including',
  'common',
  'preferred',
  'stocks',
  'warrant',
  '##s',
  'similar',
  'rights',
  'purchase',
  'company',
  '##s',
  'securities',
  'convertible',
  'securities',
  'issued',
  'non',
  'u',
  's',
  'companies',
  'the',
  'fund',
  'may',
  'invest',
  'securities',
  'traded',
  'mature',
  'markets',
  'example',
  'japan',
  'germany',
  'france',
  'countries',
  'whose',
  'economies',
  'still',
  'developing',
  'sometimes',
  'called',
  'emerging',
  'markets',
  'the',
  'fund',
  'particularly',
  'seeks',
  'companies',
  'financial',
  'strength',
  'stability',
  'strong',
  'management',
  'fundamental',
  'value',
  'fundamental',
  'value',
  'term',
  'commonly',
  'used',
  'value',
  'investors',
  'refer',
  'estimate',
  'value',
  'educated',
  'buyer',
  'would',
  'place',
  'company',
  'whole',
  'normally',
  'fund',
  'invest',
  '